# Autoeval inference testing

In [ ]:
from transformers import AutoProcessor, AutoTokenizer, AutoModelForCausalLM
import torch
import os

try:
    from google.colab import userdata
    HF_TOKEN = userdata.get('HF_TOKEN')
    os.environ['HF_TOKEN'] = HF_TOKEN
except:
    print("Not running in Google Colab, trying to get the HF_TOKEN from the environment")


if os.environ.get('HF_TOKEN') is None:
    raise ValueError("You must set the HF_TOKEN environment variable to use this script, you also need to have access to the Llama 3.2 model family")

hugging_face_model_id = "eltorio/Llama-3.2-3B-appreciation"
base_model_path = "meta-llama/Llama-3.2-3B-Instruct"
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')


## Load the model

In [2]:
processor = AutoProcessor.from_pretrained(
    base_model_path,
    do_image_splitting=False
)

model = AutoModelForCausalLM.from_pretrained(
    base_model_path,
    torch_dtype=torch.float16,
    low_cpu_mem_usage=True,
).to(device)
model.load_adapter(hugging_face_model_id)
tokenizer = AutoTokenizer.from_pretrained(hugging_face_model_id)

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

## Define a function for getting a multiturn conversation

In [ ]:
# Define a function to infer a evaluation from the incoming parameters
def infere(trimestre: str, moyenne_1: float,moyenne_2: float,moyenne_3: float, comportement: float, participation: float, travail: float) -> str:

    if trimestre == "1":
        trimestre_full = "premier trimestre"
        user_question = f"Veuillez rédiger une appréciation en moins de 40 mots pour le {trimestre_full} pour cet élève qui a eu {moyenne_1} de moyenne, j'ai évalué son comportement à {comportement}/10, sa participation à {participation}/10 et son travail à {travail}/10. Les notes ne doivent pas apparaître dans l'appréciation."
    elif trimestre == "2":
        trimestre_full = "deuxième trimestre"
        user_question = f"Veuillez rédiger une appréciation en moins de 40 mots pour le {trimestre_full} pour cet élève qui a eu {moyenne_2} de moyenne ce trimestre et {moyenne_1} au premier trimestre, j'ai évalué son comportement à {comportement}/10, sa participation à {participation}/10 et son travail à {travail}/10. Les notes ne doivent pas apparaître dans l'appréciation."
    elif trimestre == "3":
        trimestre_full = "troisième trimestre"
        user_question= f"Veuillez rédiger une appréciation en moins de 40 mots pour le {trimestre_full} pour cet élève qui a eu {moyenne_3} de moyenne ce trimestre, {moyenne_2} au deuxième trimestre et {moyenne_1} au premier trimestre, j'ai évalué son comportement à {comportement}/10, sa participation à {participation}/10 et son travail à {travail}/10. Les notes ne doivent pas apparaître dans l'appréciation."
    messages = [
        {
            "role": "system",
            "content": "Vous êtes une IA assistant les enseignants d'histoire-géographie en rédigeant à leur place une appréciation personnalisée pour leur élève en fonction de ses performances. Votre appreciation doit être en français, et doit aider l'élève à comprendre ses points forts et les axes d'amélioration. Votre appréciation doit comporter de 1 à 40 mots. Votre appréciation ne doit jamais comporter la valeur de la note. Votre appréciation doit utiliser le style impersonnel.Attention l'élément le plus important de votre analyse doit rester la moyenne du trimestre"},
        {
            "role": "user",
            "content": user_question},
    ]
    return messages

In [4]:
messages = infere("1", 3, float('nan'), float('nan'), 10, 10, 10)

## Tokenize the input

In [5]:
inputs = tokenizer.apply_chat_template(
        messages,
        tokenize = True,
        add_generation_prompt = True,
        return_tensors = "pt",).to(device)
inputs

tensor([[128000, 128006,   9125, 128007,    271,  38766,   1303,  33025,   2696,
             25,   6790,    220,   2366,     18,    198,  15724,   2696,     25,
            220,   1627,   5887,    220,   2366,     19,    271,  43273,  62299,
           6316,  44190,  18328,   3625,  68061,    625,   1821,    294,      6,
          90446,   2427,    978,   3257,    648,    665,   9517,     67,   7404,
            519,   3869,  28130,   2035,   6316,    917,  43711,   5979,    367,
          97252,  35965,   8047,   5019,  28130,  33013,  79351,    665,  34501,
            409,  15907,  24601,     13,    650,  52262,  35996,  42182,  23761,
            665,  55467,     11,   1880,  42182,  91878,    326,      6,  19010,
          79351,   3869,  60946,    265,  15907,   3585,  75652,   1880,   3625,
          25776,    294,  58591,  73511,   7769,     13,    650,  52262,    917,
          43711,   5979,    367,  42182,  52962,    261,    409,    220,     16,
           3869,    220,   1

## Generate the output

In [6]:
outputs = model.generate(input_ids = inputs, 
                                        max_new_tokens = 90, 
                                        use_cache = True,
                                        temperature = 1.5,
                                        min_p = 0.1,
                                        pad_token_id=tokenizer.eos_token_id,)
decoded_sequences = tokenizer.batch_decode(outputs[:, inputs.shape[1]:],skip_special_tokens=True)[0]
decoded_sequences

The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


"Quel changement (positif) par rapport à l'an passé! X travaille plus sérieusement, il fait davantage d'effort, il participe. Son redoublement lui permettra d'avoir une deuxième année plus confortable. Continuer ainsi devrait payer au final."